In [1]:
import tensorflow as tf
import numpy as np
import pandas as pd
import scipy.integrate as integrate

def xavier_init(size):
    in_dim = size[0]
    out_dim = size[1]
    xavier_stdev = np.sqrt(2/(in_dim + out_dim))
    return tf.Variable(tf.random.truncated_normal([in_dim*out_dim], stddev=xavier_stdev), dtype = tf.float32)

def initialize_NN(layers):
    num_layers = len(layers)
    weights = tf.Variable([], dtype=tf.float32)
    biases = tf.Variable([], dtype=tf.float32)
    for l in range(len(layers)-1):
        W = xavier_init(size = [layers[l], layers[l+1]])
        b = tf.Variable(tf.zeros([layers[l+1]], dtype=tf.float32), tf.float32)
        weights = tf.concat([weights, W], 0)
        biases = tf.concat([biases, b], 0)
    return tf.concat([weights, biases], 0)

def convert_params(params):
    lower_range = 0
    upper_range = lower_range + layers[0]*layers[1]
    weights = []
    for l in range(1, len(layers)-1):
        weights.append(tf.reshape(params[lower_range:upper_range], [layers[l-1],layers[l]]))
        lower_range = upper_range
        upper_range += layers[l]*layers[l+1]
    weights.append(tf.reshape(params[lower_range:upper_range], [layers[-2], layers[-1]]))
    biases = []
    for l in range(1, len(layers)):
        lower_range = upper_range
        upper_range += layers[l]
        biases.append(tf.reshape(params[lower_range:upper_range],[1,layers[l]]))
    return weights, biases

def predict(weights, biases, inputs):
    num_layers = len(weights) + 1
    H = (2.0*(inputs-lb)/(ub-lb)-1.0)
    H = tf.cast(H, tf.float32)
    for l in range(num_layers-2):
        W = weights[l]
        b = biases[l]
        H = tf.tanh(tf.add(tf.matmul(H,W), b))
    W = weights[-1]
    b = biases[-1]
    return tf.add(tf.matmul(H, W), b)

In [2]:
# Initialize matrices/constants
vis = .01/np.pi # Viscocity term in Burger's equation
n_x = 500 # Number of u(x, t) elements on x
X = np.zeros(n_x)
Y1 = np.zeros(n_x)
Y2 = np.zeros(n_x)
Y3 = np.zeros(n_x)
Y4 = np.zeros(n_x)
Y5 = np.zeros(n_x)
Y6 = np.zeros(n_x)
Y7 = np.zeros(n_x)
Y8 = np.zeros(n_x)
Y9 = np.zeros(n_x)
Y_ani = np.zeros(n_x)

# Analytical solution for Burger's equation with periodic boundary conditions 
# at x = [-5,5] and initial condition u(x,0) = -sin(pi*x)
def f_cole(y):
    return np.exp(-np.cos(np.pi*y)/(2*np.pi*vis))

def integrand1(eta, x, t):
    return np.sin(np.pi*(x-eta))*f_cole(x-eta)*np.exp(-eta**2/(4*vis*t))

def integrand2(eta, x, t):
    return f_cole(x-eta)*np.exp(-eta**2/(4*vis*t))

def u_anal(x, t):
    if t == 0:
        return -np.sin(np.pi*x)
    else:
        I1 = integrate.quad(integrand1, -np.inf, np.inf, args=(x,t))[0]
        I2 = integrate.quad(integrand2, -np.inf, np.inf, args=(x,t))[0]
        return -I1/I2
    
def gen_train(max_t, set_size=500):
    m = int(set_size/2)
    tr_init = np.zeros([m,3])
    tr_bound = np.zeros([m,3])
    
    tr_init[:,1] = np.linspace(-5, 5, m)
    tr_bound[:,1] = np.ones(m) - 2*np.random.randint(2, size=m)
    tr_bound[:,2] = np.linspace(0, max_t, m)
    for i in range(m):
        tr_init[i][0] = u_anal(tr_init[i][1], 0)
        tr_bound[i][0] = u_anal(tr_bound[i][1], tr_bound[i][2])
    training = np.append(tr_init, tr_bound, axis=0)
    df = pd.DataFrame(training, columns=['u(x,t)', 'x', 't'])
    return df

train_df = gen_train(500)

<ipython-input-2-9cf9a9b791b4>:31: IntegrationWarning: The integral is probably divergent, or slowly convergent.
  I1 = integrate.quad(integrand1, -np.inf, np.inf, args=(x,t))[0]
<ipython-input-2-9cf9a9b791b4>:31: IntegrationWarning: The maximum number of subdivisions (50) has been achieved.
  If increasing the limit yields no improvement it is advised to analyze 
  the integrand in order to determine the difficulties.  If the position of a 
  local difficulty can be determined (singularity, discontinuity) one will 
  probably gain from splitting up the interval and calling the integrator 
  on the subranges.  Perhaps a special-purpose integrator should be used.
  I1 = integrate.quad(integrand1, -np.inf, np.inf, args=(x,t))[0]


In [3]:
X_train = tf.cast(tf.convert_to_tensor(train_df.iloc[:,1:]), dtype=tf.float32)
Y_train = tf.cast(tf.reshape(tf.convert_to_tensor(train_df.iloc[:,0]), [500,1]), tf.float32)

ub = (X_train).numpy().max(0)
lb = (X_train).numpy().min(0)

def loss(parameters, callback=False):
    lambda_1 = parameters[0]
    parameters = parameters[1:]
    x_tf = tf.reshape(X_train[:,0], [500, 1])
    t_tf = tf.reshape(X_train[:,1], [500, 1])
    
    weights, biases = convert_params(parameters)
    with tf.GradientTape() as tape:
        tape.watch(x_tf)
        with tf.GradientTape(persistent=True) as tape2:
            tape2.watch(x_tf)
            tape2.watch(t_tf)
            u_pred = predict(weights,  biases, tf.concat([x_tf, t_tf], 1))
        u_x = tape2.gradient(u_pred, x_tf)
        u_t = tape2.gradient(u_pred, t_tf)
    u_xx = tape.gradient(u_x, x_tf)
    f = u_t + u_pred*u_x - lambda_1*u_xx
    f_error = tf.reduce_sum(tf.square(f))
    pred_error = tf.reduce_sum(tf.square(u_pred - Y_train))
    if callback:
        print("F_Error: {}\t Pred_Error: {}\tLambda: {}".format(f_error, pred_error, lambda_1))
    return f_error + pred_error

In [4]:
layers = [2, 20, 20, 20, 20, 20, 20, 1]
parameters = initialize_NN(layers)
optimizer = tf.keras.optimizers.Adam()
lambda_val = tf.convert_to_tensor([0.0], dtype=tf.float32)
parameters = tf.concat([lambda_val, parameters], 0)
parameters = tf.Variable(parameters)

adam_loss = lambda: loss(parameters)

for itr in range(250000):
    optimizer.minimize(adam_loss, parameters)
    if itr % 10 == 0:
        itr_loss = loss(parameters, callback=True)
        print("Itr: {}\tLoss: {}".format(itr, itr_loss))

F_Error: 0.0060989451594650745	 Pred_Error: 135.31224060058594	Lambda: -0.0009991712868213654
Itr: 0	Loss: 135.31834411621094
F_Error: 0.00048714192234911025	 Pred_Error: 122.3740234375	Lambda: -0.006665636785328388
Itr: 10	Loss: 122.37451171875
F_Error: 0.006983180996030569	 Pred_Error: 122.6163558959961	Lambda: -0.0007062484510242939
Itr: 20	Loss: 122.62333679199219
F_Error: 0.0031192232854664326	 Pred_Error: 122.18513488769531	Lambda: 0.010469150729477406
Itr: 30	Loss: 122.1882553100586
F_Error: 0.00108742481097579	 Pred_Error: 122.15193939208984	Lambda: 0.018990308046340942
Itr: 40	Loss: 122.15303039550781
F_Error: 0.0015675969189032912	 Pred_Error: 122.07659912109375	Lambda: 0.02456461824476719
Itr: 50	Loss: 122.07816314697266
F_Error: 0.002331798430532217	 Pred_Error: 122.04402160644531	Lambda: 0.029545532539486885
Itr: 60	Loss: 122.04635620117188
F_Error: 0.0021756531205028296	 Pred_Error: 122.02645111083984	Lambda: 0.03517046570777893
Itr: 70	Loss: 122.02862548828125
F_Error: 0

F_Error: 0.3436245918273926	 Pred_Error: 117.66191864013672	Lambda: -0.15331892669200897
Itr: 670	Loss: 118.00554656982422
F_Error: 0.30372220277786255	 Pred_Error: 116.80105590820312	Lambda: -0.15180419385433197
Itr: 680	Loss: 117.10477447509766
F_Error: 0.315986692905426	 Pred_Error: 116.7994384765625	Lambda: -0.15152433514595032
Itr: 690	Loss: 117.11542510986328
F_Error: 0.3438436686992645	 Pred_Error: 116.71441650390625	Lambda: -0.15058590471744537
Itr: 700	Loss: 117.05825805664062
F_Error: 0.3431895673274994	 Pred_Error: 116.71178436279297	Lambda: -0.150469571352005
Itr: 710	Loss: 117.05497741699219
F_Error: 0.33960944414138794	 Pred_Error: 116.70698547363281	Lambda: -0.151920884847641
Itr: 720	Loss: 117.04659271240234
F_Error: 0.3451222777366638	 Pred_Error: 116.69355010986328	Lambda: -0.1528298258781433
Itr: 730	Loss: 117.0386734008789
F_Error: 0.3494805097579956	 Pred_Error: 116.68299102783203	Lambda: -0.15353156626224518
Itr: 740	Loss: 117.032470703125
F_Error: 0.3512213826179

F_Error: 0.3860659897327423	 Pred_Error: 116.49240112304688	Lambda: -0.17905519902706146
Itr: 1340	Loss: 116.87846374511719
F_Error: 0.38745906949043274	 Pred_Error: 116.48979187011719	Lambda: -0.17960241436958313
Itr: 1350	Loss: 116.87725067138672
F_Error: 0.5142055749893188	 Pred_Error: 123.28678894042969	Lambda: -0.17867209017276764
Itr: 1360	Loss: 123.80099487304688
F_Error: 0.3185383677482605	 Pred_Error: 118.11524963378906	Lambda: -0.17269457876682281
Itr: 1370	Loss: 118.43378448486328
F_Error: 0.3290039002895355	 Pred_Error: 116.81744384765625	Lambda: -0.17330771684646606
Itr: 1380	Loss: 117.14644622802734
F_Error: 0.3787103593349457	 Pred_Error: 116.67244720458984	Lambda: -0.17262472212314606
Itr: 1390	Loss: 117.05115509033203
F_Error: 0.36044126749038696	 Pred_Error: 116.64042663574219	Lambda: -0.1710372120141983
Itr: 1400	Loss: 117.00086975097656
F_Error: 0.35352829098701477	 Pred_Error: 116.61112976074219	Lambda: -0.17135831713676453
Itr: 1410	Loss: 116.96466064453125
F_Erro

F_Error: 0.3936491310596466	 Pred_Error: 116.44375610351562	Lambda: -0.18758834898471832
Itr: 2010	Loss: 116.83740234375
F_Error: 0.3940728008747101	 Pred_Error: 116.44100952148438	Lambda: -0.188017800450325
Itr: 2020	Loss: 116.8350830078125
F_Error: 0.39129340648651123	 Pred_Error: 116.44168853759766	Lambda: -0.18846316635608673
Itr: 2030	Loss: 116.8329849243164
F_Error: 0.39406919479370117	 Pred_Error: 116.4365005493164	Lambda: -0.1889573037624359
Itr: 2040	Loss: 116.83056640625
F_Error: 0.4185680150985718	 Pred_Error: 116.42151641845703	Lambda: -0.18917407095432281
Itr: 2050	Loss: 116.840087890625
F_Error: 0.3850266933441162	 Pred_Error: 116.44459533691406	Lambda: -0.18962469696998596
Itr: 2060	Loss: 116.82962036132812
F_Error: 0.3982846736907959	 Pred_Error: 116.42617797851562	Lambda: -0.1900022029876709
Itr: 2070	Loss: 116.824462890625
F_Error: 0.40249425172805786	 Pred_Error: 116.42160034179688	Lambda: -0.19037006795406342
Itr: 2080	Loss: 116.8240966796875
F_Error: 0.443621307611

F_Error: 0.3980853259563446	 Pred_Error: 116.41340637207031	Lambda: -0.19427180290222168
Itr: 2680	Loss: 116.81149291992188
F_Error: 0.39850491285324097	 Pred_Error: 116.41099548339844	Lambda: -0.19465850293636322
Itr: 2690	Loss: 116.80950164794922
F_Error: 0.3989214599132538	 Pred_Error: 116.40860748291016	Lambda: -0.1950419396162033
Itr: 2700	Loss: 116.80752563476562
F_Error: 0.3993277847766876	 Pred_Error: 116.40625762939453	Lambda: -0.1954222470521927
Itr: 2710	Loss: 116.80558776855469
F_Error: 0.3997339606285095	 Pred_Error: 116.40392303466797	Lambda: -0.19579948484897614
Itr: 2720	Loss: 116.80365753173828
F_Error: 0.4001283347606659	 Pred_Error: 116.40159606933594	Lambda: -0.19617390632629395
Itr: 2730	Loss: 116.80172729492188
F_Error: 0.40048888325691223	 Pred_Error: 116.39933776855469	Lambda: -0.19654573500156403
Itr: 2740	Loss: 116.7998275756836
F_Error: 0.40075698494911194	 Pred_Error: 116.3971939086914	Lambda: -0.19691550731658936
Itr: 2750	Loss: 116.7979507446289
F_Error: 0

...

F_Error: 11.046675682067871	 Pred_Error: 30.59920883178711	Lambda: 0.02332179993391037
Itr: 247160	Loss: 41.6458854675293
F_Error: 11.57656478881836	 Pred_Error: 31.066598892211914	Lambda: 0.023235531523823738
Itr: 247170	Loss: 42.643165588378906
F_Error: 11.008749961853027	 Pred_Error: 30.697969436645508	Lambda: 0.02312733419239521
Itr: 247180	Loss: 41.70671844482422
F_Error: 13.973501205444336	 Pred_Error: 31.41290855407715	Lambda: 0.02315116673707962
Itr: 247190	Loss: 45.386409759521484
F_Error: 11.207525253295898	 Pred_Error: 30.740642547607422	Lambda: 0.023229798302054405
Itr: 247200	Loss: 41.94816589355469
F_Error: 11.508090019226074	 Pred_Error: 30.31865119934082	Lambda: 0.02333500050008297
Itr: 247210	Loss: 41.82674026489258
F_Error: 11.13934326171875	 Pred_Error: 30.474504470825195	Lambda: 0.02335311844944954
Itr: 247220	Loss: 41.61384582519531
F_Error: 11.085531234741211	 Pred_Error: 30.354917526245117	Lambda: 0.023320985957980156
Itr: 247230	Loss: 41.44044876098633
F_Error: 

F_Error: 11.034777641296387	 Pred_Error: 28.101564407348633	Lambda: 0.020571505650877953
Itr: 247820	Loss: 39.1363410949707
F_Error: 11.09263801574707	 Pred_Error: 27.96432113647461	Lambda: 0.02055848017334938
Itr: 247830	Loss: 39.05696105957031
F_Error: 12.749482154846191	 Pred_Error: 28.962312698364258	Lambda: 0.02045353315770626
Itr: 247840	Loss: 41.711795806884766
F_Error: 18.512067794799805	 Pred_Error: 29.09619903564453	Lambda: 0.01971219666302204
Itr: 247850	Loss: 47.60826873779297
F_Error: 11.713543891906738	 Pred_Error: 29.94951057434082	Lambda: 0.020172446966171265
Itr: 247860	Loss: 41.663055419921875
F_Error: 11.160269737243652	 Pred_Error: 29.627979278564453	Lambda: 0.02041267789900303
Itr: 247870	Loss: 40.78824996948242
F_Error: 11.429859161376953	 Pred_Error: 28.765657424926758	Lambda: 0.020116712898015976
Itr: 247880	Loss: 40.195518493652344
F_Error: 11.019257545471191	 Pred_Error: 28.820274353027344	Lambda: 0.020715873688459396
Itr: 247890	Loss: 39.83953094482422
F_Erro

F_Error: 10.80282211303711	 Pred_Error: 26.202606201171875	Lambda: 0.025624649599194527
Itr: 248480	Loss: 37.005428314208984
F_Error: 10.82093620300293	 Pred_Error: 26.05889129638672	Lambda: 0.0261685810983181
Itr: 248490	Loss: 36.87982940673828
F_Error: 10.866778373718262	 Pred_Error: 25.856855392456055	Lambda: 0.026485232636332512
Itr: 248500	Loss: 36.7236328125
F_Error: 10.841461181640625	 Pred_Error: 25.739025115966797	Lambda: 0.02670586109161377
Itr: 248510	Loss: 36.58048629760742
F_Error: 10.78311824798584	 Pred_Error: 25.685321807861328	Lambda: 0.026928743347525597
Itr: 248520	Loss: 36.468441009521484
F_Error: 10.825379371643066	 Pred_Error: 25.530214309692383	Lambda: 0.027102135121822357
Itr: 248530	Loss: 36.355594635009766
F_Error: 10.813810348510742	 Pred_Error: 25.429832458496094	Lambda: 0.027271371334791183
Itr: 248540	Loss: 36.24364471435547
F_Error: 10.793214797973633	 Pred_Error: 25.331432342529297	Lambda: 0.02742009609937668
Itr: 248550	Loss: 36.12464904785156
F_Error: 

F_Error: 12.423104286193848	 Pred_Error: 28.878965377807617	Lambda: 0.02713080868124962
Itr: 249150	Loss: 41.30207061767578
F_Error: 10.481375694274902	 Pred_Error: 28.194580078125	Lambda: 0.024138325825333595
Itr: 249160	Loss: 38.67595672607422
F_Error: 10.428045272827148	 Pred_Error: 26.68211555480957	Lambda: 0.025600505992770195
Itr: 249170	Loss: 37.11016082763672
F_Error: 10.543910026550293	 Pred_Error: 25.398950576782227	Lambda: 0.025818729773163795
Itr: 249180	Loss: 35.9428596496582
F_Error: 9.917765617370605	 Pred_Error: 25.28179168701172	Lambda: 0.026563623920083046
Itr: 249190	Loss: 35.19955825805664
F_Error: 9.92952823638916	 Pred_Error: 24.667123794555664	Lambda: 0.0264113862067461
Itr: 249200	Loss: 34.59665298461914
F_Error: 9.581372261047363	 Pred_Error: 24.399532318115234	Lambda: 0.026676660403609276
Itr: 249210	Loss: 33.98090362548828
F_Error: 9.450809478759766	 Pred_Error: 23.856821060180664	Lambda: 0.027015436440706253
Itr: 249220	Loss: 33.30763244628906
F_Error: 9.237

F_Error: 11.12857723236084	 Pred_Error: 16.37541389465332	Lambda: 0.030529700219631195
Itr: 249820	Loss: 27.503990173339844
F_Error: 9.015892028808594	 Pred_Error: 19.263193130493164	Lambda: 0.02954346314072609
Itr: 249830	Loss: 28.279085159301758
F_Error: 7.12376070022583	 Pred_Error: 17.461196899414062	Lambda: 0.02927769348025322
Itr: 249840	Loss: 24.584957122802734
F_Error: 7.041553974151611	 Pred_Error: 16.577781677246094	Lambda: 0.029904259368777275
Itr: 249850	Loss: 23.619335174560547
F_Error: 6.4239888191223145	 Pred_Error: 16.821544647216797	Lambda: 0.02956376224756241
Itr: 249860	Loss: 23.245532989501953
F_Error: 6.6479034423828125	 Pred_Error: 16.1897029876709	Lambda: 0.029590552672743797
Itr: 249870	Loss: 22.83760643005371
F_Error: 6.541983127593994	 Pred_Error: 16.02220344543457	Lambda: 0.029693545773625374
Itr: 249880	Loss: 22.564186096191406
F_Error: 6.402405738830566	 Pred_Error: 15.9318208694458	Lambda: 0.029694948345422745
Itr: 249890	Loss: 22.334226608276367
F_Error: 

In [5]:
import tensorflow_probability as tfp

def val_and_gradient(params):
    print("Loss: {}".format(loss(params, callback=True)))
    return tfp.math.value_and_gradient(loss, params)

optim_results = tfp.optimizer.lbfgs_minimize(val_and_gradient, initial_position=parameters,  max_iterations=50000, max_line_search_iterations=50000)

print(optim_results.converged)
parameters = optim_results.position

F_Error: 9.706588745117188	 Pred_Error: 25.387680053710938	Lambda: 0.026163730770349503
Loss: 35.094268798828125
F_Error: 1.3414638000327885e+17	 Pred_Error: 35326.40234375	Lambda: 20.02137565612793
Loss: 1.3414638000327885e+17
F_Error: 205458149212160.0	 Pred_Error: 9657.6318359375	Lambda: 10.023770332336426
Loss: 205458149212160.0
F_Error: 14217139716096.0	 Pred_Error: 3638.035400390625	Lambda: 5.024966716766357
Loss: 14217139716096.0
F_Error: 9.706588745117188	 Pred_Error: 25.387680053710938	Lambda: 0.026163730770349503
Loss: 35.094268798828125
F_Error: 6231611670528.0	 Pred_Error: 396.7887878417969	Lambda: 2.5255653858184814
Loss: 6231611670528.0
F_Error: 9.706588745117188	 Pred_Error: 25.387680053710938	Lambda: 0.026163730770349503
Loss: 35.094268798828125
F_Error: 10.528820037841797	 Pred_Error: 25.032432556152344	Lambda: 0.026196911931037903
Loss: 35.56125259399414
F_Error: 9.726008415222168	 Pred_Error: 25.36668586730957	Lambda: 0.026165535673499107
Loss: 35.09269332885742
F_Er

F_Error: 9.491456031799316	 Pred_Error: 25.093263626098633	Lambda: 0.026480121538043022
Loss: 34.584720611572266
F_Error: 9.475773811340332	 Pred_Error: 25.088621139526367	Lambda: 0.026357589289546013
Loss: 34.564395904541016
F_Error: 9.478720664978027	 Pred_Error: 25.103139877319336	Lambda: 0.025867460295557976
Loss: 34.58185958862305
F_Error: 9.464402198791504	 Pred_Error: 25.088104248046875	Lambda: 0.02616610936820507
Loss: 34.55250549316406
F_Error: 9.462742805480957	 Pred_Error: 25.079872131347656	Lambda: 0.025956084951758385
Loss: 34.5426139831543
F_Error: 9.537129402160645	 Pred_Error: 25.09541893005371	Lambda: 0.025115983560681343
Loss: 34.63254928588867
F_Error: 9.463781356811523	 Pred_Error: 25.078330993652344	Lambda: 0.025899294763803482
Loss: 34.5421142578125
F_Error: 9.0889253616333	 Pred_Error: 25.442806243896484	Lambda: 0.02616804838180542
Loss: 34.53173065185547
F_Error: 9.237051010131836	 Pred_Error: 25.280729293823242	Lambda: 0.02605307474732399
Loss: 34.5177803039550

F_Error: 9.68120002746582	 Pred_Error: 23.989261627197266	Lambda: 0.026315132156014442
Loss: 33.67046356201172
F_Error: 9.56999397277832	 Pred_Error: 24.08488655090332	Lambda: 0.026384485885500908
Loss: 33.65488052368164
F_Error: 9.208712577819824	 Pred_Error: 24.57965660095215	Lambda: 0.026661904528737068
Loss: 33.788368225097656
F_Error: 9.539009094238281	 Pred_Error: 24.115001678466797	Lambda: 0.026404758915305138
Loss: 33.65401077270508
F_Error: 9.552329063415527	 Pred_Error: 24.09980583190918	Lambda: 0.026408037170767784
Loss: 33.65213394165039
F_Error: 9.607264518737793	 Pred_Error: 24.040252685546875	Lambda: 0.02642114832997322
Loss: 33.647518157958984
F_Error: 9.932177543640137	 Pred_Error: 23.767417907714844	Lambda: 0.026486702263355255
Loss: 33.6995964050293
F_Error: 9.631369590759277	 Pred_Error: 24.015724182128906	Lambda: 0.026426659896969795
Loss: 33.6470947265625
F_Error: 9.6842622756958	 Pred_Error: 23.953697204589844	Lambda: 0.026380429044365883
Loss: 33.63795852661133


F_Error: 10.456356048583984	 Pred_Error: 22.507251739501953	Lambda: 0.026894550770521164
Loss: 32.96360778808594
F_Error: 10.963011741638184	 Pred_Error: 22.054935455322266	Lambda: 0.027063176035881042
Loss: 33.017948150634766
F_Error: 10.509406089782715	 Pred_Error: 22.452945709228516	Lambda: 0.026915360242128372
Loss: 32.96235275268555
F_Error: 10.490004539489746	 Pred_Error: 22.4615535736084	Lambda: 0.026938708499073982
Loss: 32.95155715942383
F_Error: 10.421789169311523	 Pred_Error: 22.506195068359375	Lambda: 0.027032101526856422
Loss: 32.92798614501953
F_Error: 10.29281234741211	 Pred_Error: 22.980287551879883	Lambda: 0.027499066665768623
Loss: 33.273101806640625
F_Error: 10.406678199768066	 Pred_Error: 22.520301818847656	Lambda: 0.027056096121668816
Loss: 32.926979064941406
F_Error: 10.456250190734863	 Pred_Error: 22.464126586914062	Lambda: 0.027202237397432327
Loss: 32.92037582397461
F_Error: 10.727341651916504	 Pred_Error: 22.269390106201172	Lambda: 0.027786804363131523
Loss: 3

F_Error: 16.044368743896484	 Pred_Error: 22.528213500976562	Lambda: 0.028491122648119926
Loss: 38.57258224487305
F_Error: 10.432472229003906	 Pred_Error: 21.243900299072266	Lambda: 0.027529306709766388
Loss: 31.676372528076172
F_Error: 10.075130462646484	 Pred_Error: 21.506404876708984	Lambda: 0.027385294437408447
Loss: 31.58153533935547
F_Error: 10.342666625976562	 Pred_Error: 22.65540885925293	Lambda: 0.026809241622686386
Loss: 32.998077392578125
F_Error: 10.069477081298828	 Pred_Error: 21.511995315551758	Lambda: 0.02738223783671856
Loss: 31.581472396850586
F_Error: 10.563738822937012	 Pred_Error: 21.001882553100586	Lambda: 0.027232497930526733
Loss: 31.56562042236328
F_Error: 10.309405326843262	 Pred_Error: 21.238798141479492	Lambda: 0.027300452813506126
Loss: 31.548202514648438
F_Error: 10.301044464111328	 Pred_Error: 21.238237380981445	Lambda: 0.02732236310839653
Loss: 31.539281845092773
F_Error: 10.308401107788086	 Pred_Error: 21.264860153198242	Lambda: 0.027410004287958145
Loss:

...

F_Error: 4.630600929260254	 Pred_Error: 11.022655487060547	Lambda: 0.031523171812295914
Loss: 15.6532564163208
F_Error: 4.622592926025391	 Pred_Error: 11.030406951904297	Lambda: 0.03152529150247574
Loss: 15.652999877929688
F_Error: 4.610581874847412	 Pred_Error: 11.028244972229004	Lambda: 0.03146817162632942
Loss: 15.638826370239258
F_Error: 4.610006332397461	 Pred_Error: 11.038213729858398	Lambda: 0.031239693984389305
Loss: 15.64822006225586
F_Error: 4.60140323638916	 Pred_Error: 11.02840518951416	Lambda: 0.03137480840086937
Loss: 15.62980842590332
F_Error: 4.565731048583984	 Pred_Error: 11.06149959564209	Lambda: 0.03141981363296509
Loss: 15.627230644226074
F_Error: 4.454891681671143	 Pred_Error: 11.200345993041992	Lambda: 0.03159983456134796
Loss: 15.655237197875977
F_Error: 4.5602874755859375	 Pred_Error: 11.066868782043457	Lambda: 0.031427208334207535
Loss: 15.627156257629395
F_Error: 4.56637716293335	 Pred_Error: 11.059052467346191	Lambda: 0.031376518309116364
Loss: 15.62542915344

Loss: 15.413335800170898
F_Error: 4.647007465362549	 Pred_Error: 10.76442813873291	Lambda: 0.03167242556810379
Loss: 15.411436080932617
F_Error: 4.659446716308594	 Pred_Error: 10.763823509216309	Lambda: 0.03163914754986763
Loss: 15.423270225524902
F_Error: 4.647367000579834	 Pred_Error: 10.763608932495117	Lambda: 0.03166695311665535
Loss: 15.41097640991211
F_Error: 4.6133246421813965	 Pred_Error: 10.795571327209473	Lambda: 0.03167957440018654
Loss: 15.408895492553711
F_Error: 4.615722179412842	 Pred_Error: 10.793251037597656	Lambda: 0.031678684055805206
Loss: 15.408973693847656
F_Error: 4.610495567321777	 Pred_Error: 10.797882080078125	Lambda: 0.03174402937293053
Loss: 15.408377647399902
F_Error: 4.61189603805542	 Pred_Error: 10.796138763427734	Lambda: 0.031717699021101
Loss: 15.408035278320312
F_Error: 4.612689018249512	 Pred_Error: 10.794438362121582	Lambda: 0.031730908900499344
Loss: 15.407127380371094
F_Error: 4.618790149688721	 Pred_Error: 10.788467407226562	Lambda: 0.031783740967

F_Error: 4.603895664215088	 Pred_Error: 10.628392219543457	Lambda: 0.03161146119236946
Loss: 15.232288360595703
F_Error: 4.564032554626465	 Pred_Error: 10.622796058654785	Lambda: 0.0316820964217186
Loss: 15.18682861328125
F_Error: 4.559560775756836	 Pred_Error: 10.611653327941895	Lambda: 0.03175158426165581
Loss: 15.17121410369873
F_Error: 4.576693058013916	 Pred_Error: 10.575396537780762	Lambda: 0.03202953562140465
Loss: 15.152090072631836
F_Error: 4.56779670715332	 Pred_Error: 10.582474708557129	Lambda: 0.03196563199162483
Loss: 15.15027141571045
F_Error: 4.6035284996032715	 Pred_Error: 10.531872749328613	Lambda: 0.032064635306596756
Loss: 15.135400772094727
F_Error: 4.602749824523926	 Pred_Error: 10.532694816589355	Lambda: 0.03206291049718857
Loss: 15.135444641113281
F_Error: 4.615948677062988	 Pred_Error: 10.50259780883789	Lambda: 0.0321570485830307
Loss: 15.118546485900879
F_Error: 4.7808709144592285	 Pred_Error: 10.432044982910156	Lambda: 0.032533593475818634
Loss: 15.21291542053

F_Error: 4.605486869812012	 Pred_Error: 10.419342041015625	Lambda: 0.032093584537506104
Loss: 15.024828910827637
F_Error: 4.605215549468994	 Pred_Error: 10.419153213500977	Lambda: 0.03210228309035301
Loss: 15.024368286132812
F_Error: 4.608360290527344	 Pred_Error: 10.419781684875488	Lambda: 0.03214578703045845
Loss: 15.028141975402832
F_Error: 4.605428695678711	 Pred_Error: 10.418937683105469	Lambda: 0.032107919454574585
Loss: 15.02436637878418
F_Error: 4.644895553588867	 Pred_Error: 10.397830963134766	Lambda: 0.03232705965638161
Loss: 15.042726516723633
F_Error: 4.60942268371582	 Pred_Error: 10.413765907287598	Lambda: 0.0321507453918457
Loss: 15.023188591003418
F_Error: 4.6088056564331055	 Pred_Error: 10.413472175598145	Lambda: 0.03216312453150749
Loss: 15.02227783203125
F_Error: 4.608371257781982	 Pred_Error: 10.41161060333252	Lambda: 0.03221263736486435
Loss: 15.019981384277344
F_Error: 4.628746032714844	 Pred_Error: 10.407702445983887	Lambda: 0.032460205256938934
Loss: 15.036448478

F_Error: 4.8619465827941895	 Pred_Error: 9.990028381347656	Lambda: 0.03232370689511299
Loss: 14.851974487304688
F_Error: 4.854748249053955	 Pred_Error: 9.995877265930176	Lambda: 0.03233219310641289
Loss: 14.850625991821289
F_Error: 4.831756114959717	 Pred_Error: 10.020051002502441	Lambda: 0.03236614167690277
Loss: 14.851806640625
F_Error: 4.845035076141357	 Pred_Error: 10.004790306091309	Lambda: 0.03234509006142616
Loss: 14.849824905395508
F_Error: 4.8440704345703125	 Pred_Error: 10.004722595214844	Lambda: 0.03234301880002022
Loss: 14.848793029785156
F_Error: 4.839802265167236	 Pred_Error: 10.005575180053711	Lambda: 0.03233473747968674
Loss: 14.845376968383789
F_Error: 4.8309454917907715	 Pred_Error: 10.009784698486328	Lambda: 0.03229333087801933
Loss: 14.840730667114258
F_Error: 4.831839084625244	 Pred_Error: 10.008246421813965	Lambda: 0.03230499103665352
Loss: 14.840085983276367
F_Error: 4.814004898071289	 Pred_Error: 10.017420768737793	Lambda: 0.032296519726514816
Loss: 14.831425666

In [6]:
.01/np.pi

0.003183098861837907